In [ ]:
!pip install pymongo

In [ ]:
from bs4 import BeautifulSoup
import requests
import pandas as pd
import ast
from pymongo import MongoClient
client = MongoClient("mongodb://localhost:27017/",serverSelectionTimeoutMS=600000,  # 24.8 days
                     socketTimeoutMS=214748364)
db = client['phones_db']
collection = db['phones']
def ExtractLinks(url):
    response = requests.get(url)
    soup = BeautifulSoup(response.content, 'html.parser')
    div_block = soup.find('div', class_='sc-61baf88b-7 dRkNeo grid')
    href_links = []
    site = 'https://noon.com'
    # Check if the div with the specific class exists
    if div_block:
        href_links = [
            site + a_tag.get('href')
            for span_block in div_block.find_all('span')
            for a_tag in span_block.find_all('a')
            if a_tag.get('href')
        ]

    return href_links

In [ ]:
all_phones_pages_link_list = []
for i in range(1,20):
    page = f'https://www.noon.com/egypt-en/eg-all-mobiles/?f%5BisCarousel%5D%5B%5D=true&f%5Bis_fbn%5D%5B%5D=1&limit=50&page={i}&sort%5Bby%5D=popularity&sort%5Bdir%5D=desc'
    all_phones_pages_link_list.append(page)

In [ ]:
all_phones_pages_link_list

['https://www.noon.com/egypt-en/eg-all-mobiles/?f%5BisCarousel%5D%5B%5D=true&f%5Bis_fbn%5D%5B%5D=1&limit=50&page=1&sort%5Bby%5D=popularity&sort%5Bdir%5D=desc',
 'https://www.noon.com/egypt-en/eg-all-mobiles/?f%5BisCarousel%5D%5B%5D=true&f%5Bis_fbn%5D%5B%5D=1&limit=50&page=2&sort%5Bby%5D=popularity&sort%5Bdir%5D=desc',
 'https://www.noon.com/egypt-en/eg-all-mobiles/?f%5BisCarousel%5D%5B%5D=true&f%5Bis_fbn%5D%5B%5D=1&limit=50&page=3&sort%5Bby%5D=popularity&sort%5Bdir%5D=desc',
 'https://www.noon.com/egypt-en/eg-all-mobiles/?f%5BisCarousel%5D%5B%5D=true&f%5Bis_fbn%5D%5B%5D=1&limit=50&page=4&sort%5Bby%5D=popularity&sort%5Bdir%5D=desc',
 'https://www.noon.com/egypt-en/eg-all-mobiles/?f%5BisCarousel%5D%5B%5D=true&f%5Bis_fbn%5D%5B%5D=1&limit=50&page=5&sort%5Bby%5D=popularity&sort%5Bdir%5D=desc',
 'https://www.noon.com/egypt-en/eg-all-mobiles/?f%5BisCarousel%5D%5B%5D=true&f%5Bis_fbn%5D%5B%5D=1&limit=50&page=6&sort%5Bby%5D=popularity&sort%5Bdir%5D=desc',
 'https://www.noon.com/egypt-en/eg-all-m

In [ ]:
all_phones_links=[]
headers = {
    "User-Agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/78.0.3904.108 Safari/537.36",
    "Accept-Encoding": "gzip, deflate",
    "Accept": "text/html,application/xhtml+xml,application/xml;q=0.9,*/*;q=0.8",
    "DNT": "1",
    "Connection": "close",
    "Upgrade-Insecure-Requests": "1",
}

def get_all_phones_link(link):
    page = requests.get(link,headers=headers)
    soup = BeautifulSoup(page.content, "html.parser")
    all_phones = soup.find_all("div", class_="sc-57fe1f38-0 eSrvHE")
    print(all_phones)
    for phone in all_phones:
        phone_link = phone.find("a").get("href")
        phone_link = f"https://www.noon.com{phone_link}"
        all_phones_links.append(phone_link)

In [ ]:
for page_link in all_phones_pages_link_list:
    get_all_phones_link(page_link)

[<div class="sc-57fe1f38-0 eSrvHE"><a href="/egypt-en/galaxy-a05s-dual-sim-black-4gb-ram-64gb-4g-lte-middle-east-version-with-a-free-gift-25w-adapter-usb-c-super-fast-charging-travel-adapter-eu-plug/N70112983V/p/?o=f9c78efaf122cd4f" id="productBox-N70112983V"><div class="sc-57fe1f38-1 gYzxDm grid"><div class="sc-95ea18ef-0 jJTgts"><div class="sc-95ea18ef-1 lnIWRf"><div data-qa="productImagePLP_Galaxy A05s Dual SIM Black 4GB RAM 64GB 4G LTE - Middle East Version with a free gift 25W Adapter USB-C Super Fast Charging Travel Adapter (EU Plug) "><div class="sc-8aa199cf-0 cXXinA"><div class="sc-8aa199cf-4 fLkTPR"><div class="sc-95ea18ef-3 rVcLc"><div class="sc-95ea18ef-9 jEpNXt"><div class="sc-95ea18ef-10 eeCEjZ"><div class="sc-1196519d-0 haoIxB"><span class="sc-1196519d-1 ggVSNh">Official Warranty</span></div></div></div><div class="sc-95ea18ef-11 iqwzSQ"><div class="sc-95ea18ef-12 fUOnum"><button class="sc-95ea18ef-14 dqkiMm" type="button"><img alt="wishlist" class="sc-92fbb12b-1 GgDWC" h

In [ ]:
len(all_phones_links)



878

In [ ]:


def get_phone_data(link):
    # Default values for missing data
    default_data = {
        "Name": "unknown-product",
        "Main Image": "No cover Image",
        "Other Images": ["No other Images for the cover"],
        "Price ": "No Price",
        "Number of Sells": "No Data",
        "Ratings": "No Ratings",
        "Number of Ratings": "No Ratings",
        "Description": ["No cover description"],
        "About the Product": ["No About the cover data"],
        "Reviews": []
    }

    # Check if the link is a placeholder URL
    if link == "https://www.noon.com/javascript:void(0)":
        return pd.DataFrame([default_data])

    # Fetch and parse the page content
    page = requests.get(link)
    soup = BeautifulSoup(page.content, "html.parser")

    # Extract product name
    name_element = soup.find('h1', class_='sc-f35b8612-22 jBencA')
    phone_name = name_element.get_text(strip=True) if name_element else default_data["Name"]

    # Extract company name (if needed, update the default data)
    brand_element = soup.find('div', class_='sc-f35b8612-21 ovuGP')
    company_name = brand_element.get_text(strip=True) if brand_element else "unknown-brand"

    # Extract images from the page
    container = soup.find('div', class_='lazyload-wrapper')
    main_image_url = default_data["Main Image"]
    other_images = []

    if container:
        # Find the main image inside the specific container
        main_img_div = container.find('div', class_='sc-d8caf424-2 fJBKzl')
        if main_img_div:
            img = main_img_div.find('img')
            if img:
                main_image_url = img.get('src')

    all_images = soup.find_all('img')
    for img in all_images:
        img_url = img.get('src')
        if img_url != main_image_url:
            other_images.append(img_url)

    # Extract model number
    model_number_div = soup.find('div', class_='modelNumber')
    model_number = model_number_div.get_text(strip=True) if model_number_div else "No Model Number"

    # Extract rating
    rating_div = soup.find('div', class_='sc-9cb63f72-2 dGLdNc')
    rating = rating_div.get_text(strip=True) if rating_div else default_data["Ratings"]

    # Extract number of ratings
    ratings_count_span = soup.find('span', class_='sc-9cb63f72-5 DkxLK')
    ratings_count = ratings_count_span.get_text(strip=True) if ratings_count_span else default_data["Number of Ratings"]

    # Extract price
    price_div = soup.find('div', class_='priceNow')
    price = price_div.get_text(strip=True) if price_div else None


    # Extract description
    description_div = soup.find('div', class_='sc-97eb4126-2 oPZpQ')
    description_list = [item.get_text(strip=True) for item in description_div.find_all('li')] if description_div else default_data["Description"]

    specs_div = soup.find('div', class_='sc-966c8510-2 dROUvm')
    specifications = {}
    if specs_div:
        table = specs_div.find('table')
        if table:
            rows = table.find_all('tr')
            for row in rows:
                cols = row.find_all('td')
                if len(cols) == 2:
                    key = cols[0].get_text(strip=True)
                    value = cols[1].get_text(strip=True)
                    specifications[key] = value

    phone_data = {
        "Name": phone_name,
        "campany": company_name,
        "Main Image": main_image_url,
        "Other Images": other_images if other_images else default_data["Other Images"],
        "Price ": price,
        "model": model_number,
        "Ratings": rating,
        "Number of Ratings": ratings_count,
        "Description": description_list,
        "About the Product": specifications,
    }

    # Convert to DataFrame
    phone_df = pd.DataFrame([phone_data])

    return phone_df


In [ ]:
phones_data = []

for page_link in all_phones_links:
    df = get_phone_data(page_link)
    phones_data.append(df)

all_phones_df = pd.concat(phones_data, ignore_index=True)
print(all_phones_df)

                                                  Name  campany  \
0    Galaxy A05s Dual SIM Black 4GB RAM 64GB 4G LTE...  Samsung   
1    Galaxy A15 Dual Sim Blue Black 4GB RAM 128GB 4...  Samsung   
2    A70 Dual SIM  Field Green (3+5)GB RAM 128GB 4G...     ITEL   
3    Galaxy A15 Dual Sim Light Blue 4GB RAM 128GB 4...  Samsung   
4    Galaxy A15 Dual SIM Blue/Black 6GB RAM 128GB 4...  Samsung   
..                                                 ...      ...   
873  real me C65 Dual SIM Starlight Black 8 GB RAM ...   realme   
874  realme C61 Dual SIM Dark Green 8 GB RAM 256 GB...   realme   
875          V40 Lite 4G Dual SIM Silver 8GB RAM 256GB     vivo   
876  Galaxy-A16 Dual SIM Light Green 8GB RAM 256GB ...  Samsung   
877  Y19s Dual SIM Silver 4GB RAM 128GB 4G - Middle...     vivo   

         Main Image                                       Other Images  \
0    No cover Image  [https://f.nooncdn.com/s/app/com/noon/design-s...   
1    No cover Image  [https://f.nooncdn.com/s/a

In [ ]:
data=pd.DataFrame(all_phones_df)


In [ ]:
gf= get_phone_data('https://www.noon.com/egypt-en/galaxy-s24-ultra-dual-sim-titanium-gray-12gb-ram-256gb-5g-middle-east-version/N70035206V/p/?o=e91fe343f84fd02d')

In [ ]:
gf

Name  campany      Main Image  \
0  Galaxy S24 Ultra Dual SIM Titanium Gray 12GB R...  Samsung  No cover Image   

                                        Other Images  \
0  [https://f.nooncdn.com/s/app/com/noon/design-s...   

                        Price                                      model  \
0  EGP49999.00Inclusive of VAT  Model Number:SM-S928BZTCMEA, SM-S928B/DS   

  Ratings Number of Ratings  \
0     4.6              3.8K   

                                         Description  \
0  [The samsung galaxy S24 is universally use the...   

                                   About the Product  
0  {'Secondary Camera Resolution': '12 MP', 'Char...

In [ ]:

client = MongoClient("mongodb://6.tcp.eu.ngrok.io:19632")
db = client['phones_db']
collection = db['phones']
for col in data.columns:
    data.rename(columns={col: col.strip()}, inplace=True)

data['Price'] = data['Price'].astype(str).str.extract(r'(\d+\.\d+|\d+)')[0].astype(float)

data['model'] = data['model'].str.replace('Model Number:', '').str.strip()

data.drop(columns=['Description'], inplace=True)

about_product = data['About the Product']
keys_to_extract = ['Secondary Camera','Primary Camera (MP)', 'RAM Size', 'Battery Size', 'Internal Memory', 'Operating System','Processor Name' ]

filtered_data = []

for row in about_product:
    filtered_dict = {}
    for key in keys_to_extract:
        filtered_dict[key] = row.get(key, None)
    filtered_data.append(filtered_dict)

about_product_df = pd.DataFrame(filtered_data)



data = pd.concat([data.drop(columns=['About the Product']), about_product_df], axis=1)

data['RAM Size'] = data['RAM Size'].str.extract(r'(\d+)').astype(float)

data['Battery Size'] = data['Battery Size'].str.extract(r'(\d+)').astype(float)

data['Internal Memory'] = data['Internal Memory'].str.extract(r'(\d+)').astype(float)
collection.insert_many(data.to_dict('records'))
print("Cleaned data has been saved to MongoDB.")


Cleaned data has been saved to MongoDB.
